In [6]:
import torch
import os
import cv2 as cv
import numpy as np
import pandas as pd
import torchvision
from torch.utils.data import Dataset, DataLoader
import matplotlib.pyplot as plt
import albumentations
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
import seaborn as sns
import torchvision.transforms as transforms
import torchvision.models as models
from PIL import Image
from tqdm import tqdm

In [7]:
def compute_iou(box_pred, box_true):
    """
    box_pred, box_true: tensors có shape (B, 4) với định dạng [x_center, y_center, w, h]
    Giá trị đã được chuẩn hóa trong khoảng [0, 1]
    """
    # Chuyển từ [xc, yc, w, h] sang [x1, y1, x2, y2]
    pred_x1 = box_pred[:, 0] - box_pred[:, 2] / 2
    pred_y1 = box_pred[:, 1] - box_pred[:, 3] / 2
    pred_x2 = box_pred[:, 0] + box_pred[:, 2] / 2
    pred_y2 = box_pred[:, 1] + box_pred[:, 3] / 2

    true_x1 = box_true[:, 0] - box_true[:, 2] / 2
    true_y1 = box_true[:, 1] - box_true[:, 3] / 2
    true_x2 = box_true[:, 0] + box_true[:, 2] / 2
    true_y2 = box_true[:, 1] + box_true[:, 3] / 2

    # Tính tọa độ của vùng giao nhau
    inter_x1 = torch.max(pred_x1, true_x1)
    inter_y1 = torch.max(pred_y1, true_y1)
    inter_x2 = torch.min(pred_x2, true_x2)
    inter_y2 = torch.min(pred_y2, true_y2)

    inter_area = torch.clamp(inter_x2 - inter_x1, min=0) * torch.clamp(inter_y2 - inter_y1, min=0)
    pred_area = (pred_x2 - pred_x1) * (pred_y2 - pred_y1)
    true_area = (true_x2 - true_x1) * (true_y2 - true_y1)

    union_area = pred_area + true_area - inter_area
    iou = inter_area / (union_area + 1e-6)

    return iou.mean().item()  # Trả về IoU trung bình


In [8]:
def compute_accuracy(class_logits, labels):
    """
    class_logits: output từ model (B, num_classes)
    labels: ground-truth labels (B,)
    """
    preds = torch.argmax(class_logits, dim=1)
    correct = (preds == labels).sum().item()
    total = labels.size(0)
    accuracy = correct / total
    return accuracy


In [9]:

class RandomChannelShift:
    def __init__(self, shift_range):
        self.shift_range = shift_range

    def __call__(self, img):
        shift = np.random.uniform(-self.shift_range, self.shift_range)
        img = np.array(img).astype(np.float32)
        img += shift
        img = np.clip(img, 0, 255)
        return Image.fromarray(img.astype(np.uint8))


def get_image_and_label_paths(base_path, classes):
    image_paths = []
    label_paths = []
    labels = []

    for cls in classes:
        img_dir = os.path.join(base_path, cls, "images")
        label_dir = os.path.join(base_path, cls, "labels")

        for fname in os.listdir(img_dir):
            if fname.lower().endswith(('.jpg', '.jpeg', '.png', '.bmp')):
                image_path = os.path.join(img_dir, fname)
                label_name = os.path.splitext(fname)[0] + ".txt"
                label_path = os.path.join(label_dir, label_name)

                # Check label exists, not empty, and has at least 5 values (class + bbox)
                if os.path.exists(label_path) and os.path.getsize(label_path) > 0:
                    with open(label_path, 'r') as f:
                        line = f.readline().strip().split()
                        if len(line) >= 5:
                            image_paths.append(image_path)
                            label_paths.append(label_path)
                            labels.append(cls)

    return image_paths, label_paths, labels


class BrainTumorDataset(Dataset):
    def __init__(self, image_paths, label_paths, label_indices, transform=None):
        self.image_paths = image_paths
        self.label_paths = label_paths
        self.label_indices = label_indices
        self.transform = transform

    def __len__(self):
        return len(self.image_paths)

    def __getitem__(self, idx):
        image = Image.open(self.image_paths[idx]).convert("RGB")
        label = self.label_indices[idx]

        # Load bounding box
        with open(self.label_paths[idx], 'r') as f:
            line = f.readline().strip().split()
            if len(line) < 5:
                raise ValueError(f"Invalid bbox in file: {self.label_paths[idx]}")
            bbox = list(map(float, line[1:]))  # skip class_id

        if self.transform:
            image = self.transform(image)

        bbox = torch.tensor(bbox, dtype=torch.float32)
        label = torch.tensor(label, dtype=torch.long)

        return image, label, bbox


def prepare_data(train_path, classes, img_size=(224, 224), batch_size=64):
    image_paths, label_paths, labels = get_image_and_label_paths(train_path, classes)

    label_encoder = LabelEncoder()
    encoded_labels = label_encoder.fit_transform(labels)

    train_img, val_img, train_lbl, val_lbl, train_box, val_box = train_test_split(
        image_paths, encoded_labels, label_paths, test_size=0.2, random_state=42, stratify=encoded_labels
    )

    train_transform = transforms.Compose([
        transforms.Resize(img_size),
        transforms.RandomHorizontalFlip(),
        transforms.RandomVerticalFlip(),
        transforms.ColorJitter(brightness=0.1),
        RandomChannelShift(10.0),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.5]*3, std=[0.5]*3)
    ])

    val_transform = transforms.Compose([
        transforms.Resize(img_size),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.5]*3, std=[0.5]*3)
    ])

    train_dataset = BrainTumorDataset(train_img, train_box, train_lbl, transform=train_transform)
    val_dataset = BrainTumorDataset(val_img, val_box, val_lbl, transform=val_transform)

    train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False)

    return train_loader, val_loader, label_encoder


In [10]:
train_path = "/content/drive/MyDrive/Brain_tumors_MRIs_with_bounding_box/Train"
classes = ["Glioma", "Meningioma", "No Tumor", "Pituitary"]

train_loader, val_loader, label_encoder = prepare_data(train_path, classes)

print("Train batches:", len(train_loader))
print("Val batches:", len(val_loader))
print("Number of classes:", len(classes))
print("Class mapping:", dict(enumerate(label_encoder.classes_)))


Train batches: 60
Val batches: 15
Number of classes: 4
Class mapping: {0: np.str_('Glioma'), 1: np.str_('Meningioma'), 2: np.str_('No Tumor'), 3: np.str_('Pituitary')}


In [11]:
import torch
import torch.nn as nn
import torchvision.models as models

class MultiHeaded(nn.Module):
    def __init__(self, num_classes = 4, preTrained = True):
        super(MultiHeaded, self).__init__()

        resnet = models.resnet50(pretrained=preTrained)

        self.backbone = nn.Sequential(*list(resnet.children())[:-1])  # Output shape: (batch_size, 2048, 1, 1)

        # Flatten layer
        self.flatten = nn.Flatten()

        # Classification head (output 4 class logits)
        self.classifier = nn.Sequential(
          nn.Linear(2048, 512),
          nn.ReLU(),
          nn.Dropout(0.3),
          nn.Linear(512, num_classes)
        )
        # Localization head (predict [x_center, y_center, w, h], all normalized)
        self.localization = nn.Sequential(
          nn.Linear(2048, 512),
          nn.ReLU(),
          nn.Dropout(0.3),
          nn.Linear(512, 4),
          nn.Sigmoid()  # đảm bảo đầu ra trong khoảng [0,1] nếu bbox đã được chuẩn hóa
        )

    def forward(self, x):
        features = self.backbone(x)     # (B, 2048, 1, 1)
        features = self.flatten(features)  # (B, 2048)

        class_logits = self.classifier(features)     # (B, 4)
        bbox_preds = self.localization(features)     # (B, 4)

        return class_logits, bbox_preds

In [12]:
def train_model(model, train_loader, val_loader, num_epochs=10, lr=1e-4, lambda_bbox=5.0, device='cuda'):
    model = model.to(device)

    criterion_class = nn.CrossEntropyLoss()
    criterion_bbox = nn.MSELoss()
    optimizer = torch.optim.Adam(model.parameters(), lr=lr)

    for epoch in range(num_epochs):
        model.train()
        running_loss = 0.0
        train_loop = tqdm(train_loader, desc=f"Epoch [{epoch+1}/{num_epochs}] Training", leave=False)

        for images, labels, bboxes in train_loop:
            images = images.to(device)
            labels = labels.to(device)
            bboxes = bboxes.to(device)

            class_logits, bbox_preds = model(images)

            loss_class = criterion_class(class_logits, labels)
            loss_bbox = criterion_bbox(bbox_preds, bboxes)
            loss = loss_class + lambda_bbox * loss_bbox

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

            running_loss += loss.item()
            train_loop.set_postfix(loss=loss.item())

        avg_train_loss = running_loss / len(train_loader)

        # Validation phase
        model.eval()
        val_loss = 0.0
        val_loop = tqdm(val_loader, desc=f"Epoch [{epoch+1}/{num_epochs}] Validation", leave=False)
        with torch.no_grad():
            for images, labels, bboxes in val_loop:
                images = images.to(device)
                labels = labels.to(device)
                bboxes = bboxes.to(device)

                class_logits, bbox_preds = model(images)

                loss_class = criterion_class(class_logits, labels)
                loss_bbox = criterion_bbox(bbox_preds, bboxes)
                loss = loss_class + lambda_bbox * loss_bbox

                val_loss += loss.item()
                val_loop.set_postfix(val_loss=loss.item())

        avg_val_loss = val_loss / len(val_loader)

        print(f"Epoch [{epoch+1}/{num_epochs}] "
              f"Train Loss: {avg_train_loss:.4f} | Val Loss: {avg_val_loss:.4f}")


In [13]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Khởi tạo model
model = MultiHeaded(num_classes=4, preTrained=True)
model = model.to(device)  # Đưa model lên GPU (nếu có)

# Huấn luyện mô hình
train_model(model, train_loader, val_loader, num_epochs=10, lr=1e-4, lambda_bbox=5.0, device=device)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/resnet50-0676ba61.pth" to /root/.cache/torch/hub/checkpoints/resnet50-0676ba61.pth
100%|██████████| 97.8M/97.8M [00:00<00:00, 168MB/s]


Epoch [1/10] Train Loss: 0.4942 | Val Loss: 0.2440


Epoch [2/10] Train Loss: 0.1555 | Val Loss: 0.1512


Epoch [3/10] Train Loss: 0.1015 | Val Loss: 0.1055


Epoch [4/10] Train Loss: 0.0737 | Val Loss: 0.0665


...

Epoch [6/10] Train Loss: 0.0574 | Val Loss: 0.0501


Epoch [7/10] Train Loss: 0.0476 | Val Loss: 0.0743


Epoch [8/10] Train Loss: 0.0502 | Val Loss: 0.0952


Epoch [9/10] Train Loss: 0.0576 | Val Loss: 0.0821


Epoch [10/10] Train Loss: 0.0448 | Val Loss: 0.0520


In [14]:
def prepare_test_loader(test_path, classes, label_encoder, img_size=(224, 224), batch_size=32):
    image_paths, label_paths, labels = get_image_and_label_paths(test_path, classes)

    # Encode labels using the same encoder as training
    encoded_labels = label_encoder.transform(labels)

    # Use validation-like transform (no augmentation)
    test_transform = transforms.Compose([
        transforms.Resize(img_size),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.5]*3, std=[0.5]*3)
    ])

    test_dataset = BrainTumorDataset(image_paths, label_paths, encoded_labels, transform=test_transform)
    test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False)

    return test_loader


In [16]:
classes = ["Glioma", "Meningioma", "No Tumor", "Pituitary"]
test_path = '/content/drive/MyDrive/Brain_tumors_MRIs_with_bounding_box/Val'
test_loader = prepare_test_loader(test_path, classes, label_encoder)


In [19]:
from sklearn.metrics import accuracy_score, classification_report
def compute_iou(box1, box2):
    # box format: [x_center, y_center, w, h], normalized
    x1_min = box1[0] - box1[2] / 2
    y1_min = box1[1] - box1[3] / 2
    x1_max = box1[0] + box1[2] / 2
    y1_max = box1[1] + box1[3] / 2

    x2_min = box2[0] - box2[2] / 2
    y2_min = box2[1] - box2[3] / 2
    x2_max = box2[0] + box2[2] / 2
    y2_max = box2[1] + box2[3] / 2

    # Intersection
    inter_xmin = max(x1_min, x2_min)
    inter_ymin = max(y1_min, y2_min)
    inter_xmax = min(x1_max, x2_max)
    inter_ymax = min(y1_max, y2_max)

    inter_area = max(0, inter_xmax - inter_xmin) * max(0, inter_ymax - inter_ymin)

    area1 = (x1_max - x1_min) * (y1_max - y1_min)
    area2 = (x2_max - x2_min) * (y2_max - y2_min)

    union_area = area1 + area2 - inter_area
    iou = inter_area / (union_area + 1e-6)
    return iou

def evaluate_model(model, dataloader, device, label_encoder):
    model.eval()
    all_preds = []
    all_labels = []
    all_boxes_gt = []
    all_boxes_pred = []
    ious = []

    with torch.no_grad():
        for images, labels, boxes in tqdm(dataloader, desc="Evaluating"):
            images = images.to(device)
            labels = labels.to(device)
            boxes = boxes.to(device)

            # Forward pass
            class_logits, bbox_preds = model(images)

            # Classification prediction
            preds = torch.argmax(class_logits, dim=1)

            # Collect for metrics
            all_preds.extend(preds.cpu().numpy())
            all_labels.extend(labels.cpu().numpy())

            gt_boxes = boxes.cpu().numpy()
            pred_boxes = bbox_preds.cpu().numpy()
            all_boxes_gt.extend(gt_boxes)
            all_boxes_pred.extend(pred_boxes)

            # Compute IoUs for each sample in batch
            for gt, pred in zip(gt_boxes, pred_boxes):
                iou = compute_iou(gt, pred)
                ious.append(iou)

    # Classification metrics
    acc = accuracy_score(all_labels, all_preds)
    report = classification_report(all_labels, all_preds, target_names=label_encoder.classes_)

    # IoU metrics
    ious = np.array(ious)
    mean_iou = np.mean(ious)
    median_iou = np.median(ious)
    percent_below_07 = np.sum(ious < 0.7) / len(ious) * 100

    print(f"\nTest Accuracy: {acc * 100:.2f}%")
    print(f"Mean IoU: {mean_iou:.4f}")
    print(f"Median IoU: {median_iou:.4f}")
    print(f"IoU < 0.7: {percent_below_07:.2f}% of predictions")
    print("\nClassification Report:\n", report)

    return {
        'accuracy': acc,
        'mean_iou': mean_iou,
        'median_iou': median_iou,
        'percent_iou_below_07': percent_below_07,
        'all_preds': all_preds,
        'all_labels': all_labels,
        'all_boxes_gt': all_boxes_gt,
        'all_boxes_pred': all_boxes_pred,
        'ious': ious.tolist()
    }


In [20]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

# Gọi hàm evaluate
results = evaluate_model(model, test_loader, device, label_encoder)

# Truy cập các thành phần cụ thể:
accuracy = results['accuracy']
ious = results['ious']
median_iou = results['median_iou']
percent_low_iou = results['percent_iou_below_07']

Evaluating: 100%|██████████| 16/16 [00:07<00:00,  2.24it/s]


Test Accuracy: 99.61%
Mean IoU: 0.2939
Median IoU: 0.1657
IoU < 0.7: 81.34% of predictions

Classification Report:
               precision    recall  f1-score   support

      Glioma       1.00      0.99      1.00       135
  Meningioma       0.99      1.00      0.99       140
    No Tumor       1.00      1.00      1.00        98
   Pituitary       1.00      0.99      1.00       136

    accuracy                           1.00       509
   macro avg       1.00      1.00      1.00       509
weighted avg       1.00      1.00      1.00       509



In [22]:
def load_val_dataset(val_path, classes, label_encoder, img_size=(224, 224)):
    val_img, val_label_paths, val_labels = get_image_and_label_paths(val_path, classes)
    val_encoded = label_encoder.transform(val_labels)

    val_transform = transforms.Compose([
        transforms.Resize(img_size),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.5]*3, std=[0.5]*3)
    ])

    val_dataset = BrainTumorDataset(val_img, val_label_paths, val_encoded, transform=val_transform)
    return val_dataset


In [23]:
val_path = "/content/drive/MyDrive/Brain_tumors_MRIs_with_bounding_box/Val"
classes = ['Glioma', 'Meningioma', 'No Tumor', 'Pituitary']

val_dataset = load_val_dataset(val_path, classes, label_encoder)

In [24]:
import cv2
import matplotlib.pyplot as plt
import numpy as np
import torch

def yolo_to_xyxy(box, img_width, img_height):
    x_c, y_c, w, h = box
    x1 = (x_c - w / 2) * img_width
    y1 = (y_c - h / 2) * img_height
    x2 = (x_c + w / 2) * img_width
    y2 = (y_c + h / 2) * img_height
    return [x1, y1, x2, y2]

def intersection_over_union_yolo(box1, box2):
    # box1, box2: YOLO format [x_center, y_center, w, h]
    box1_xyxy = yolo_to_xyxy(box1, 1.0, 1.0)
    box2_xyxy = yolo_to_xyxy(box2, 1.0, 1.0)

    xA = max(box1_xyxy[0], box2_xyxy[0])
    yA = max(box1_xyxy[1], box2_xyxy[1])
    xB = min(box1_xyxy[2], box2_xyxy[2])
    yB = min(box1_xyxy[3], box2_xyxy[3])

    interArea = max(0, xB - xA) * max(0, yB - yA)
    if interArea == 0:
        return 0.0

    box1_area = (box1_xyxy[2] - box1_xyxy[0]) * (box1_xyxy[3] - box1_xyxy[1])
    box2_area = (box2_xyxy[2] - box2_xyxy[0]) * (box2_xyxy[3] - box2_xyxy[1])
    union = box1_area + box2_area - interArea

    return interArea / union

@torch.no_grad()
def display_images_with_boxes_yolo(model, dataset, label_encoder, device, n=5, iou_threshold=0.5):
    model.eval()
    fig = plt.figure(figsize=(n * 4, 4))

    indices = np.random.choice(len(dataset), size=n, replace=False)

    for i, idx in enumerate(indices):
        image, label_true, bbox_true = dataset[idx]
        image_input = image.unsqueeze(0).to(device)

        # Dự đoán
        pred_class_logits, pred_bbox = model(image_input)
        pred_label = torch.argmax(pred_class_logits, dim=1).item()
        pred_bbox = pred_bbox[0].cpu().numpy()
        bbox_true = bbox_true.numpy()

        iou = intersection_over_union_yolo(pred_bbox, bbox_true)

        # Chuyển ảnh sang dạng hiển thị
        img_np = image.permute(1, 2, 0).cpu().numpy()
        img_np = (img_np * 0.5 + 0.5) * 255.0
        img_np = img_np.astype(np.uint8).copy()
        h, w = img_np.shape[:2]

        # Chuyển bbox sang tọa độ ảnh
        box_true_xyxy = yolo_to_xyxy(bbox_true, w, h)
        box_pred_xyxy = yolo_to_xyxy(pred_bbox, w, h)

        # Vẽ bbox
        cv2.rectangle(img_np, (int(box_true_xyxy[0]), int(box_true_xyxy[1])),
                      (int(box_true_xyxy[2]), int(box_true_xyxy[3])), (0, 255, 0), 2)  # xanh lá
        cv2.rectangle(img_np, (int(box_pred_xyxy[0]), int(box_pred_xyxy[1])),
                      (int(box_pred_xyxy[2]), int(box_pred_xyxy[3])), (255, 0, 0), 2)  # đỏ

        # Hiển thị
        ax = fig.add_subplot(1, n, i + 1)
        ax.imshow(img_np)
        ax.set_xticks([])
        ax.set_yticks([])

        true_cls = label_encoder.inverse_transform([label_true.item()])[0]
        pred_cls = label_encoder.inverse_transform([pred_label])[0]
        title = f"True: {true_cls} | Pred: {pred_cls}\nIoU: {iou:.2f}"

        if pred_label != label_true.item() or iou < iou_threshold:
            ax.set_title(title, color='red')
        else:
            ax.set_title(title, color='black')


In [28]:
display_images_with_boxes_yolo(model, val_dataset, label_encoder, device, n=100, iou_threshold=0.5)